In [13]:
# | default_exp tsfeatures.ts2image

In [14]:
# %load_ext jupyter_ai_magics

In [15]:
# %%ai ollama:llama3.2:1b
# Explain Recurrence Plot with mathemetical equation and where it is used?

In [16]:
# | export
import json  # For saving labels in a single JSON file
import os
import shutil
import warnings
from datetime import datetime, timedelta

import lightning.pytorch as pl
import numpy as np
import pandas as pd
import plotly.graph_objects as go
import torch
import torch.nn as nn
import torchvision.transforms as transforms
from PIL import Image
from plotly.subplots import make_subplots
from pyts.image import GramianAngularField, MarkovTransitionField, RecurrencePlot
from sklearn.preprocessing import LabelEncoder, MinMaxScaler, StandardScaler
from torch.utils.data import DataLoader, Dataset, Subset, random_split
from tqdm import tqdm

warnings.simplefilter("ignore", category=UserWarning)
from tqdm import tqdm

tqdm.pandas()
torch.set_float32_matmul_precision("medium")

In [17]:
# | export


def transform_to_images(ts_series):
    ts_series = ts_series.dropna().values  # Drop NaNs safely
    ts_series = ts_series.reshape(-1, 1)  # Reshape for pyts compatibility

    # Apply MinMax Scaling
    scaler = MinMaxScaler(feature_range=(0, 1))
    ts_series = scaler.fit_transform(ts_series).reshape(1, -1)

    # Generate images
    rp = RecurrencePlot().fit_transform(ts_series)[0]  # RP Image
    gaf = GramianAngularField(method="summation").fit_transform(ts_series)[0]  # GAF Image
    mtf = MarkovTransitionField().fit_transform(ts_series)[0]  # MTF Image

    return torch.stack(
        [
            torch.tensor(rp, dtype=torch.float32),
            torch.tensor(gaf, dtype=torch.float32),
            torch.tensor(mtf, dtype=torch.float32),
        ]
    )

In [18]:
# | export


def plot_ts2img(ts_series):
    timestamps = ts_series.index
    rp_image, gaf_image, mtf_image = transform_to_images(ts_series)

    # Create RGB composite image
    rgb_image = torch.stack([rp_image, gaf_image, mtf_image]).permute(1, 2, 0).numpy()  # (H, W, 3)

    # Normalize RGB image to [0, 1] for visualization
    rgb_image = (rgb_image - rgb_image.min()) / (rgb_image.max() - rgb_image.min())

    # Create subplots (3 rows, 2 columns)
    fig = make_subplots(
        rows=3,
        cols=2,
        subplot_titles=[
            "Original Time Series",
            "Combined RGB Image",
            "Gramian Angular Field (GAF)",
            "Markov Transition Field (MTF)",
            "Recurrence Plot (RP)",
        ],
    )

    # 🟢 Plot Time Series (Top-Left)
    fig.add_trace(
        go.Scatter(
            x=timestamps,
            y=ts_series,
            mode="lines+markers",
            line=dict(color="blue"),
            name="Time Series",
        ),
        row=1,
        col=1,
    )

    # 🔵 Plot Recurrence Plot (RP) (Top-Right)
    fig.add_trace(
        go.Heatmap(z=rp_image.numpy(), colorscale="gray", name="Recurrence Plot", showscale=False),
        row=3,
        col=1,
    )

    # 🟠 Plot Gramian Angular Field (GAF) (Middle-Left)
    fig.add_trace(
        go.Heatmap(
            z=gaf_image.numpy(), colorscale="gray", name="Gramian Angular Field", showscale=False
        ),
        row=2,
        col=1,
    )

    # 🔴 Plot Markov Transition Field (MTF) (Middle-Right)
    fig.add_trace(
        go.Heatmap(
            z=mtf_image.numpy(), colorscale="gray", name="Markov Transition Field", showscale=False
        ),
        row=2,
        col=2,
    )

    # 🌈 Plot RGB Composite Image (Bottom-Center)
    fig.add_trace(
        go.Heatmap(
            z=rgb_image[:, :, 0],  # Use the red channel as intensity
            colorscale="rainbow",
            name="RGB Composite",
            showscale=False,
        ),
        row=1,
        col=2,
    )

    # Customize layout
    fig.update_layout(
        title_text="Time Series & Image Transformations", height=1000, width=1200, showlegend=False
    )

    fig.show()

In [19]:
# | hide
from ts.utils.data import generate_time_series

ts_series = generate_time_series(
    n_points=200, trend_slope=0.07, seasonality_period=12, seasonality_amplitude=9, noise_std=0.9
)
plot_ts2img(ts_series)

In [20]:
# | export


def transform_tensor2img(
    df, data_dir="model_classification", categorical_label=True, label_col="best_model"
):
    """
    Transform images and save them along with their labels.

    Args:
        df (pd.DataFrame): DataFrame containing the ts in wide format.
        data_dir (str): Directory where the images will be saved.
        categorical_label (bool): Whether the label is categorical.
        label_col (str): Column name for labels.
    """
    # Create directory for storing data
    df = df.copy(deep=True)
    # Delete the directory if it exists
    if os.path.exists(data_dir):
        shutil.rmtree(data_dir)

    # Create a new directory
    os.makedirs(data_dir, exist_ok=True)

    if categorical_label:
        le = LabelEncoder()
        df[label_col] = le.fit_transform(df[label_col].values)
        class_dict = {idx: label for idx, label in enumerate(le.classes_)}
        with open(os.path.join(data_dir, "classes.json"), "w") as f:
            json.dump(class_dict, f)

    labels = df[label_col].to_dict()

    # Drop the label column from the DataFrame
    df.drop([label_col], axis=1, inplace=True)

    # Dictionary to store labels
    labels_dict = {}

    for idx, row in tqdm(df.iterrows(), total=len(df), desc="Transforming & Saving (X, y)"):

        img_tensor = transform_to_images(
            row
        )  # Ensure this returns a torch tensor of shape (3, seq_len, seq_len)

        # Convert to PIL image
        img_pil = transforms.ToPILImage()(img_tensor)

        # Save image
        img_path = os.path.join(data_dir, f"{idx}.png")
        img_pil.save(img_path)

        # Store label in dictionary
        labels_dict[idx] = labels[row.name]

    with open(os.path.join(data_dir, "labels.json"), "w") as f:
        json.dump(labels_dict, f)

In [21]:
# | export


def transform_ts2img_tensor(df, label_col, data_dir="processed_data", categorical_label=False):
    df = df.copy(deep=True)

    # Delete the directory if it exists
    if os.path.exists(data_dir):
        shutil.rmtree(data_dir)

    # Create a new directory
    os.makedirs(data_dir, exist_ok=True)

    if categorical_label:
        le = LabelEncoder()
        df[label_col] = le.fit_transform(df[label_col].values)
        class_dict = {idx: label for idx, label in enumerate(le.classes_)}
        with open(os.path.join(data_dir, "classes.json"), "w") as f:
            json.dump(class_dict, f)

    labels = df[label_col].to_dict()
    df.drop([label_col], axis=1, inplace=True)

    # Save (image, label) pairs
    for idx, series in tqdm(df.iterrows(), total=len(df), desc="Transforming & Saving (X, y)"):
        if isinstance(series.values[0], pd.Series):
            tensors = [transform_to_images(series.iloc[col]) for col in range(len(series))]

            # Find the minimum sequence length
            min_seq_len = min(tensor.shape[-1] for tensor in tensors)

            # Truncate tensors to the minimum size
            truncated_tensors = [tensor[..., :min_seq_len] for tensor in tensors]

            img_tensor = torch.cat(truncated_tensors, dim=0)  # Concatenate along batch/feature dim
        else:
            img_tensor = transform_to_images(series)  # Ensure this returns a torch tensor

        sample = {
            "image": img_tensor,
            "label": torch.tensor(labels[series.name], dtype=torch.long),
        }

        with open(os.path.join(data_dir, f"{idx}.pt"), "wb") as f:
            torch.save(sample, f)  # Save both X and y together

In [22]:
# | hide
from ts.tsfeatures.ts2image import transform_tensor2img, transform_ts2img_tensor
from ts.utils.data import generate_time_series

ts_series = generate_time_series(
    n_points=300, trend_slope=0.2, seasonality_period=7, seasonality_amplitude=4, noise_std=5
)
df = pd.DataFrame(ts_series).transpose()
df.loc[:, "target"] = 2

transform_ts2img_tensor(
    df.copy(deep=True), data_dir="test_classification", categorical_label=False, label_col="target"
)
# transform_tensor2img(
#     df.copy(deep=True), data_dir="test_classification", categorical_label=False, label_col="target"
# )

Transforming & Saving (X, y): 100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 222.26it/s]
